In [1]:
%%bash
docker-compose up -d influxdb

influxdb is up-to-date


In [2]:
import requests
requests.post(url="http://localhost:8086/query", params={'q':'CREATE DATABASE "mydb"'})

<Response [200]>

In [3]:
p = "foo bar=NaN"
r = requests.post(url="http://localhost:8086/write?db=mydb", data=p)
r.text

'{"error":"unable to parse \'foo bar=NaN\': invalid number"}\n'

In [4]:
p1 = "foo bar=1.0,baz=1.0"
p2 = "foo baz=2.0"
p3 = "foo bar=3.0,baz=3.0"
requests.post(url="http://localhost:8086/write?db=mydb", data=p1)
requests.post(url="http://localhost:8086/write?db=mydb", data=p2)
requests.post(url="http://localhost:8086/write?db=mydb", data=p3)

<Response [204]>

In [5]:
r = requests.get(url="http://localhost:8086/query", params={'q': 'SELECT * FROM "mydb"."autogen"."foo"'})
r.json()['results'][0]['series']

[{'name': 'foo',
  'columns': ['time', 'bar', 'baz'],
  'values': [['2021-03-15T17:15:06.512124262Z', 1, 1],
   ['2021-03-15T17:15:06.528977245Z', None, 2],
   ['2021-03-15T17:15:06.532419286Z', 3, 3]]}]

In [6]:
r = requests.get(url="http://localhost:8086/query", params={'q': 'SELECT mean(baz), mean(baz) FROM "mydb"."autogen"."foo" GROUP BY time(10ms) fill(linear)'})
r.json()['results'][0]['series']

[{'name': 'foo',
  'columns': ['time', 'mean', 'mean_1'],
  'values': [['2021-03-15T17:15:06.51Z', 1, 1],
   ['2021-03-15T17:15:06.52Z', 2, 2],
   ['2021-03-15T17:15:06.53Z', 3, 3],
   ['2021-03-15T17:15:06.54Z', None, None],
   ['2021-03-15T17:15:06.55Z', None, None]]}]

In [7]:
from aioinflux import InfluxDBClient
client = InfluxDBClient(db="mydb", output="dataframe")
await client.query('SELECT * FROM foo')

bar  baz
2021-03-15 17:15:06.512124262+00:00  1.0    1
2021-03-15 17:15:06.528977245+00:00  NaN    2
2021-03-15 17:15:06.532419286+00:00  3.0    3